In [4]:
import zipfile,os,re,time
import pandas as pd
from pathlib import Path

#设置工作目录, 要求工作目录中恰有一些.tex(.txt)文件和一些.zip文件，对应的文件名需相同, 其余不论
filepath = "数据导入作业文件"

# date = str(time.localtime().tm_year)+str(time.localtime().tm_mon).zfill(2)+str(time.localtime().tm_mday).zfill(2)
date = "20230523"

#生成文件列表
files = [os.path.join(filepath,f) for f in os.listdir(filepath)]
file_pairs = []
for zf in [f for f in files if ".zip" in f]:
    tf = [f for f in files if (".tex" in f or ".txt" in f) and zf[:-4] in f][0]
    file_pairs.append((zf,tf))


outputstr = "usages\n\n"
for fp in file_pairs:
    #生成文件名tex_file和zip_file
    zip_file, tex_file = fp

    newdate = input(os.path.split(zip_file)[-1][:-4]+"使用日期("+date+", 不变按回车, 要变化仅需输入最后几位改变的数字):")
    newdate = "".join(re.findall(r"\d",newdate))
    change_len = len(newdate)
    date = date[:8-change_len]+newdate

    #获得题号数据，保存在problems_list中
    with open(tex_file,"r",encoding = "utf8") as f:
        tex_data = f.read()
    problems_list = re.findall(r"\(([\d]{6})\)",tex_data)

    #在zip文件中找到包含正确率数据的文件
    zf = zipfile.ZipFile(zip_file)
    statfiles = [f.filename for f in zf.filelist if "试题分析" in f.filename]

    #生成答题纸区域编号与题目ID的对应
    correspondence_dict = {}
    if "statsfile.xlsx" in os.listdir("临时文件"):
        os.remove("临时文件/statsfile.xlsx")
    extractedpath = Path(zf.extract(statfiles[0]))
    extractedpath.rename("临时文件/statsfile.xlsx")
    df = pd.read_excel("临时文件/statsfile.xlsx")
    problems_indexes = list(df[df.columns[0]][2:])
    autofill = False
    for p in problems_indexes:
        if not autofill:
            t = input(os.path.split(zip_file)[-1][:4]+"答题纸区域"+p+"的题号为(1-"+str(len(problems_list))+", a为自动对应点前的题号, u为之后完全自动对应):")
            if t.upper() == "A":
                correspondence_dict[p] = problems_list[int(re.findall(r"([\d]+?)\.",p)[0])-1]
            elif t.upper() == "U":
                correspondence_dict[p] = problems_list[int(re.findall(r"([\d]+?)\.",p)[0])-1]
                autofill = True
            elif not (int(t)<1 or int(t)>len(problems_list)):
                correspondence_dict[p] = problems_list[int(t)-1]
        else:
            correspondence_dict[p] = problems_list[int(re.findall(r"([\d]+?)\.",p)[0])-1]




    for sf in statfiles:
        #读取文件生成区域列表与难度列表
        classname = "2023届高三"+re.findall(r"高三([\d]*?)班",sf)[0].zfill(2)+"班"
        if "statsfile.xlsx" in os.listdir("临时文件"):
            os.remove("临时文件/statsfile.xlsx")
        extractedpath = Path(zf.extract(sf))
        extractedpath.rename("临时文件/statsfile.xlsx")
        df = pd.read_excel("临时文件/statsfile.xlsx")
        difficulties = list(df[df.columns[9]][2:])
        problems_indexes = list(df[df.columns[0]][2:])
        #生成该班级题目ID对应难度列表组成的字典
        class_difficulty = {}
        for i in range(len(difficulties)):
            if problems_indexes[i] in correspondence_dict:
                if not correspondence_dict[problems_indexes[i]] in class_difficulty:
                    class_difficulty[correspondence_dict[problems_indexes[i]]] = [difficulties[i]]
                else:
                    class_difficulty[correspondence_dict[problems_indexes[i]]].append(difficulties[i])
        #添加到输出字符串中
        for id in class_difficulty:
            outputstr += id + "\n" + date + "\t" + classname + "\t" + "\t".join([("%.3f" %float(v)) for v in class_difficulty[id]]) + "\n\n"

with open("临时文件/自动转换结果.txt","w",encoding = "utf8") as f:
    f.write(outputstr)
with open("../文本文件/metadata.txt","w",encoding = "utf8") as f:
    f.write(outputstr)
zf.close()

